In [8]:
import numpy as np
import pandas as pd
import itertools
from __future__ import division
import geoplotlib as glp
from geoplotlib.utils import BoundingBox, DataAccessObject
from sklearn import cluster

%matplotlib inline
pd.set_option('display.max_columns', None)

In [35]:
filePath = 'datasets/NYPD_Motor_Vehicle_Collisions_weather4.csv'

collisions = pd.read_csv(filePath)

C:\Users\Casper\Anaconda2\lib\site-packages\IPython\core\interactiveshell.py:2902: DtypeWarning: Columns (30,31) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [36]:
#mask = ((collisions['VEHICLE TYPE CODE 1'] == 'PASSENGER VEHICLE') & (pd.notnull(collisions.LOCATION)))
mask = (pd.notnull(collisions.LOCATION))

In [11]:
cols_pass_veh = collisions.loc[mask]
print "Total %d, passenger vehicles: %d" % (len(collisions), len(cols_pass_veh))

Total 769054, passenger vehicles: 347331


In [18]:
def knn(k, dataset, colums):
    md = cluster.KMeans(n_clusters=k).fit(dataset[colums])
    return md.predict(dataset[colums]),md.cluster_centers_


def encode_column(df, target_column):
    df_mod = df.copy()
    targets = pd.Series(df_mod[target_column].unique())
    map_to_int = {name: n for n, name in enumerate(targets)}
    df_mod[target_column+"_encoded"] = df_mod[target_column].replace(map_to_int)
    return (df_mod, targets)

In [30]:
k = 10
#md = KMeans(n_clusters=k).fit(cols_pass_veh[['LONGITUDE', 'LATITUDE']])

knns, centoid = knn(k, collisions.loc[mask], ['LONGITUDE', 'LATITUDE'])

result = pd.DataFrame(cols_pass_veh)# = result
result['K-mean'] = knns


print len(cols_pass_veh) 

#result.to_csv('datasets/clusters/all.csv', sep=',')

347331


In [38]:
mdata, _ = encode_column(collisions, 'CONTRIBUTING FACTOR VEHICLE 1')
mdata, _ = encode_column(mdata, 'Conditions')

k = 10

knns, centoid = knn(k, mdata.loc[mask], ['CONTRIBUTING FACTOR VEHICLE 1_encoded','Conditions_encoded'])


result = pd.DataFrame(mdata.loc[mask])
result['K-mean'] = knns

In [40]:
import geoplotlib as gpl

def get_spaced_colors(n):
    max_value = 16581375 #255**3
    interval = int(max_value / n)
    colors = [hex(I)[2:].zfill(6) for I in range(0, max_value, interval)]
    
    return [[int(i[:2], 16), int(i[2:4], 16), int(i[4:], 16), 255] for i in colors]

colormap = get_spaced_colors(k)

def coords(k):
    lat = result[result['K-mean'] == k].LATITUDE.values
    lon = result[result['K-mean'] == k].LONGITUDE.values
    
    return lat,lon
    
for i in range(2,5):
    lat, lon = coords(i)

    data = {'lon': lon, 'lat': lat}
    gpl.dot(data, color=colormap[i])

gpl.inline()

In [41]:
collisions[pd.notnull(collisions.TemperatureC)]

Unnamed: 0        DATE   TIME        BOROUGH  ZIP CODE   LATITUDE  \
41375        41375  12/31/2015   5:30         QUEENS     11420  40.681006   
41376        41376  12/31/2015   5:40            NaN       NaN  40.822145   
41377        41377  12/31/2015   5:50            NaN       NaN  40.754901   
41378        41378  12/31/2015   5:55          BRONX     10463  40.875683   
41379        41379  12/31/2015   6:45            NaN       NaN  40.754151   
41380        41380  12/31/2015   7:00      MANHATTAN     10037  40.808905   
41381        41381  12/31/2015   7:45            NaN       NaN        NaN   
41382        41382  12/31/2015   7:55            NaN       NaN        NaN   
41383        41383  12/31/2015   8:00          BRONX     10470  40.907219   
41384        41384  12/31/2015   8:00         QUEENS     11106  40.755821   
41385        41385  12/31/2015   8:00         QUEENS     11356  40.784918   
41386        41386  12/31/2015   8:00            NaN       NaN        NaN   
41387        41387  12/31/2015   8:15       BROOKLYN     11214  40.614167   
41388        41388  12/31/2015   8:15         QUEENS     11416  40.684240   
41389        41389  12/31/2015   8:15         QUEENS     11421  40.685963   
41390        41390  12/31/2015   8:15       BROOKLYN     11214  40.612216   
41391        41391  12/31/2015   8:19            NaN       NaN        NaN   
41392        41392  12/31/2015   8:30      MANHATTAN     10038  40.709872   
41393        41393  12/31/2015   8:30         QUEENS     11691  40.596001   
41394        41394  12/31/2015   8:35          BRONX     10452  40.835052   
41395        41395  12/31/2015   8:45            NaN       NaN        NaN   
41396        41396  12/31/2015   8:48         QUEENS     11435  40.692479   
41397        41397  12/31/2015   8:50       BROOKLYN     11236  40.648546   
41398        41398  12/31/2015   9:20      MANHATTAN     10010  40.740873   
41399        41399  12/31/2015   9:29      MANHATTAN     10009  40.729432   
41400        41400  12/31/2015   9:30          BRONX     10466  40.892905   
41401        41401  12/31/2015   9:30       BROOKLYN     11212  40.658355   
41402        41402  12/31/2015   9:31       BROOKLYN     11203  40.634947   
41403        41403  12/31/2015   9:38      MANHATTAN     10128  40.785191   
41404        41404  12/31/2015   9:40      MANHATTAN     10024  40.787566   
...            ...         ...    ...            ...       ...        ...   
769024      769024  07/01/2012  18:45            NaN       NaN        NaN   
769025      769025  07/01/2012  19:55       BROOKLYN     11221  40.689218   
769026      769026  07/01/2012   1:00         QUEENS     11434  40.679937   
769027      769027  07/01/2012   1:00            NaN       NaN        NaN   
769028      769028  07/01/2012   1:00          BRONX     10456  40.828729   
769029      769029  07/01/2012   1:01       BROOKLYN     11217  40.681852   
769030      769030  07/01/2012   1:03            NaN       NaN        NaN   
769031      769031  07/01/2012  20:00       BROOKLYN     11235  40.586876   
769032      769032  07/01/2012  21:00          BRONX     10452  40.841818   
769033      769033  07/01/2012  21:00      MANHATTAN     10002  40.715357   
769034      769034  07/01/2012  21:00      MANHATTAN     10018  40.759527   
769035      769035  07/01/2012  21:05      MANHATTAN     10023  40.778607   
769036      769036  07/01/2012  21:08       BROOKLYN     11212  40.672075   
769037      769037  07/01/2012  22:00      MANHATTAN     10032  40.831568   
769038      769038  07/01/2012  22:02            NaN       NaN        NaN   
769039      769039  07/01/2012   5:00      MANHATTAN     10017  40.751441   
769040      769040  07/01/2012  17:30      MANHATTAN     10035  40.807598   
769041      769041  07/01/2012  17:32       BROOKLYN     11235  40.579187   
769042      769042  07/01/2012   5:00            NaN       NaN  40.537332   
769043      769043  07/01/2012   5:00            NaN       NaN  40.533604   
7690